In [1]:
%autosave 60
%load_ext autoreload
%autoreload 2
%matplotlib inline

import sys
from pathlib import Path

Autosaving every 60 seconds


In [2]:
p = Path("../").resolve()

In [186]:
import json
import logging
import os
import pickle
import sys
from collections import Counter, OrderedDict
from copy import deepcopy
from datetime import datetime, timedelta
from io import BytesIO
from pathlib import Path
from types import ModuleType
from typing import Dict, List, Optional, Tuple, Union, cast

import cv2
import matplotlib as plt
import numpy as np
import pandas as pd
import PIL
import PIL.Image as pil_img
import seaborn as sns
import sklearn as skl
from IPython.display import Image, display
from matplotlib.patches import Rectangle
from matplotlib_inline.backend_inline import set_matplotlib_formats
from tqdm.contrib import tenumerate, tmap, tzip
from tqdm.contrib.bells import tqdm, trange
from tqdm.notebook import tqdm

In [174]:
pd.set_option("display.max_colwidth", None)
pd.set_option("display.max_columns", 15)
pd.set_option("display.max_rows", 50)
# Suitable default display for floats
pd.options.display.float_format = "{:,.2f}".format
# matplotlib options
set_matplotlib_formats("pdf", "png")
plt.rcParams["savefig.dpi"] = 75
plt.rcParams["figure.autolayout"] = False
plt.rcParams["figure.figsize"] = 10, 6
plt.rcParams["axes.labelsize"] = 18
plt.rcParams["axes.titlesize"] = 20
plt.rcParams["font.size"] = 16
plt.rcParams["lines.linewidth"] = 2.0
plt.rcParams["lines.markersize"] = 8
plt.rcParams["legend.fontsize"] = 14
plt.rcParams["text.usetex"] = True
plt.rcParams["font.family"] = "serif"
plt.rcParams["font.serif"] = "cm"
plt.rcParams["text.latex.preamble"] = "\\usepackage{subdepth}, \\usepackage{type1cm}"

# This one is optional -- change graphs to SVG only use if you don't have a
# lot of points/lines in your graphs. Can also just use ['retina'] if you
# don't want SVG.
%config InlineBackend.figure_formats = ["retina"]
set_matplotlib_formats("pdf", "png")

In [175]:
# VIDEO_PATH = Path("/shared/g-luo/geoguessr/videos").resolve()
# OUT_PATH = Path("/shared/gbiamby/geo/screenshots/screen_samples_auto").resolve()
# assert VIDEO_PATH.exists()
# assert OUT_PATH.exists()

## Game State Detection

In [16]:
# pickle.dump(frame_detections, open(OUT_PATH / "detections/178LA7LXoCs.pkl", "wb"))

### Load Detections

In [288]:
def load_detections(video_id: str) -> pd.DataFrame:
    df_framedets = pickle.load(
        open(
            f"/shared/gbiamby/geo/segment/detections/val/df_frame_dets-video_id_{video_id}.pkl",
            "rb",
        )
    )
    if "seconds" not in df_framedets.columns:
        df_framedets["seconds"] = df_framedets.frame_id.apply(lambda frame_id: frame_id / 4.0)
    if "time" not in df_framedets.columns:
        df_framedets["time"] = df_framedets.frame_id.apply(
            lambda frame_id: datetime.utcfromtimestamp(frame_id / 4.0).strftime("%H:%M:%S:%f")
        )
    return df_framedets


# load_detections("AF9uezxZDeE")

# display(df_framedets)

In [484]:
def get_categories(geoscreens_version: str = "009"):
    data = json.load(
        open(f"/home/gbiamby/proj/geoscreens/datasets/geoscreens_{geoscreens_version}/geoscreens_{geoscreens_version}.json", "r")
    )
    return data["categories"]


# Note: don't use battle_royale_wait_screen for anything, it should have been labeled as backaround
# print(cats)

In [270]:
# # Show most common sets of UI elements that appear together in a single frame
# with pd.option_context("display.max_rows", None, "display.max_columns", None):
#     display(pd.DataFrame(df_framedets.labels_set.value_counts()))

In [236]:
# with pd.option_context("display.max_rows", None, "display.max_columns", None):
# display(df_framedets[~df_framedets.ingame_trio].sort_values(["label_set_count"], ascending=False))

### Detect Game States for Each Frame

In [520]:
def apply_smoothing(df_framedets: pd.DataFrame) -> None:
    current_state = df_framedets.loc[0]["game_state"]
    buffer_size = 4
    buffer = [df_framedets.loc[0]["game_state"]] * buffer_size
    smoothed = []

    for i, row in df_framedets.iterrows():
        counter = Counter(buffer)
        current_state = counter.most_common()[0]
        smoothed.append(current_state)
        buffer.pop(0)
        buffer.append(row.game_state)

    df_framedets["game_state_smoothed"] = [s[0] for s in smoothed]


def get_segments(df_framedets: pd.DataFrame, smoothing=False) -> List[Dict]:
    current_state = "out_of_game"
    state_transitions = []
    state_key = "game_state_smoothed" if smoothing else "game_state"
    for i, row in df_framedets.iterrows():
        if current_state != "in_game" and row[state_key] == "in_game":
            state_transitions.extend(
                [
                    {
                        "state": "out_of_game",
                        "end_frame_id": row.frame_id,
                        "end_frame_sec": row.seconds,
                        "end_frame_time": row.time,
                    },
                    {
                        "state": "in_game",
                        "start_frame_id": row.frame_id,
                        "start_frame_sec": row.seconds,
                        "start_frame_time": row.time,
                    },
                ]
            )
            current_state = "in_game"
        elif current_state == "in_game":
            if row[state_key] == "in_game":
                continue
            else:
                state_transitions.extend(
                    [
                        {
                            "state": "in_game",
                            "end_frame_id": row.frame_id,
                            "end_frame_sec": row.seconds,
                            "end_frame_time": row.time,
                        },
                        {
                            "state": "out_of_game",
                            "start_frame_id": row.frame_id,
                            "start_frame_sec": row.seconds,
                        "start_frame_time": row.time,
                        },
                    ]
                )
                current_state = row[state_key]

    return state_transitions


def get_oog_segments(segments):
    i = 1
    segs = []
    while i + 1 < len(segments):
        seg = segments[i]
        seg.update(segments[i + 1])
        if seg["state"] == "out_of_game":
            segs.append(seg)
        i += 2
    return segs

In [521]:
game_state_ui_elements = OrderedDict(
    {
        "pre_game": {
            "any": [
                ["play", "left_menu_dark"],
                ["game_about_to_start_box_white", "left_menu_dark"],
                ["battle_royale_start_menu_w_logo"],
                ["game_about_to_start_box_white", "next_orange_btn"],
                ["setup_round_time_limit_box"],
            ],
            "exact": [],
        },
        "between_rounds": {
            "any": [
                ["left_menu_dark", "challenge_high_score_board"],
                ["play_next_round", "points_bar", "did_you_enjoy_this_location"],
                ["play_next_round", "points_bar_two_bars", "did_you_enjoy_this_location"],
            ],
            "exact": [
                ["in_game_mini_map", "status_bar", "points_bar", "game_title"],
            ],
        },
        "in_game": {
            "any": [
                # The ones with "in_game_mini_map" in first position will get auto-expanded:
                ["in_game_mini_map", "guess"],
                ["in_game_mini_map", "guess_grey"],
                ["in_game_mini_map", "make_a_guess"],
                ["in_game_mini_map", "place_your_pin_grey"],
                ["in_game_mini_map", "guess_w_icon_only"],
                # Won't get expanded:
                ["status_bar", "in_game_mini_map"],
                ["status_bar", "in_game_map_expanded"],
            ],
            "exact": [
                ["status_bar_white", "status_bar", "game_title"],
                ["status_bar_white", "other", "status_bar", "game_title"],
                ["game_title", "status_bar_white", "make_a_guess_expanded", "status_bar"],
            ],
        },
        "between_games": {
            "any": [
                ["left_menu_dark", "challenge_high_score_board"],
                ["points_bar", "show_high_score"],
                ["points_bar_two_bars", "show_high_score"],
                ["try_another_map", "points_bar_two_bars", "show_full_results"],
                ["points_bar_two_bars", "show_full_results"],
                ["high_score_box", "leader_board"],
            ],
            "exact": [],
        },
        "between_round_or_game_ambiguous": {
            "any": [
                ["points_bar_two_bars", "did_you_enjoy_this_location", "status_bar"],
                ["between_rounds_box_white", "did_you_enjoy_this_location", "status_bar"],
                ["points_bar_two_bars", "status_bar"],
                ["points_bar_two_bars", "status_bar", "game_title"],
                ["points_bar_two_bars", "did_you_enjoy_this_location", "status_bar", "game_title"],
                ["points_bar_two_bars", "status_bar", "share_challenge_box_white"],
                ["points_bar_two_bars", "challenge_high_score_board", "status_bar"],
                ["points_bar_two_bars", "status_bar", "game_title", "share_challenge_box_white"],
                [
                    "between_rounds_box_white",
                    "did_you_enjoy_this_location",
                    "status_bar",
                    "game_title",
                ],
                ["points_bar", "left_menu_dark"],
                ["points_bar", "did_you_enjoy_this_location"],
                ["points_bar_two_bars", "left_menu_dark"],
                ["points_bar_two_bars", "did_you_enjoy_this_location"],
                ["left_menu_dark", "status_bar", "game_title"],
                ["status_bar", "points_bar", "game_title"],
            ],
            "exact": [],
        },
        "out_of_game": {
            "any": [],
            "exact": [],
        },
        "unknown": {
            "any": [],
            "exact": [],
        },
    }
)

for state, match_types in game_state_ui_elements.items():
    for match_type, ui_element_combos in match_types.items():
        if match_type == "any" and state == "in_game":
            # expand the map / guess button combos to include all possible
            # expanded/not-expanded combinations for the in_game_map and the corresponding
            # "guess" button
            map_combos = [
                ui_combo for ui_combo in ui_element_combos if ui_combo[0] == "in_game_mini_map"
            ]
            for ui_combo in map_combos:
                guess_button_label = ui_combo[1]
                ui_element_combos.append(["in_game_mini_map", f"{guess_button_label}_expanded"])
                ui_element_combos.append(["in_game_map_expanded", guess_button_label])
                ui_element_combos.append(["in_game_map_expanded", f"{guess_button_label}_expanded"])

        # Convert the ui element lists to sets:
        match_types[match_type] = [set(elements) for elements in ui_element_combos]


def classify_frame(dets: dict) -> str:
    """
    Input is a row of a pd.DataFrame. The row contains object detector output
    for the geoguessr UI elements.
    """
    label_set = set(dets["labels_set"])
    if len(label_set) == 0:
        return "out_of_game"

    for state, match_types in game_state_ui_elements.items():
        for ui_combo in match_types["exact"]:
            if ui_combo == label_set:
                return state

        for ui_combo in match_types["any"]:
            intersection = ui_combo.intersection(label_set)
            if len(ui_combo) == len(intersection):
                return state

    return "unknown"


# game_state_ui_elements

---

## Debug

In [533]:
video_id = "dY1RXh-43q4"
video_id = "o8qQAjkaXMM"

df_framedets = load_detections(video_id)
df_framedets["game_state"] = df_framedets.apply(classify_frame, axis=1)
apply_smoothing(df_framedets)
seg = get_segments(df_framedets, smoothing =False)
seg_oog = get_oog_segments(seg)

for s in seg:
    print(s)
print("")
print("")
for s in seg_oog:
    print(s)

{'state': 'out_of_game', 'end_frame_id': 189, 'end_frame_sec': 47.25, 'end_frame_time': '00:00:47:250000'}
{'state': 'in_game', 'start_frame_id': 189, 'start_frame_sec': 47.25, 'start_frame_time': '00:00:47:250000', 'end_frame_id': 199, 'end_frame_sec': 49.75, 'end_frame_time': '00:00:49:750000'}
{'state': 'in_game', 'end_frame_id': 199, 'end_frame_sec': 49.75, 'end_frame_time': '00:00:49:750000'}
{'state': 'out_of_game', 'start_frame_id': 199, 'start_frame_sec': 49.75, 'start_frame_time': '00:00:49:750000', 'end_frame_id': 203, 'end_frame_sec': 50.75, 'end_frame_time': '00:00:50:750000'}
{'state': 'out_of_game', 'end_frame_id': 203, 'end_frame_sec': 50.75, 'end_frame_time': '00:00:50:750000'}
{'state': 'in_game', 'start_frame_id': 203, 'start_frame_sec': 50.75, 'start_frame_time': '00:00:50:750000', 'end_frame_id': 204, 'end_frame_sec': 51.0, 'end_frame_time': '00:00:51:000000'}
{'state': 'in_game', 'end_frame_id': 204, 'end_frame_sec': 51.0, 'end_frame_time': '00:00:51:000000'}
{'sta

### Total Frames Per Game States

In [534]:
pd.DataFrame(df_framedets.game_state.value_counts())

game_state
unknown         3435
in_game          272
pre_game          43

### Show ui combos that result in game_state "unknown":

In [535]:
pd.DataFrame(
    df_framedets[df_framedets.game_state == "unknown"]
    .groupby(["labels_set"])
    .agg(cnt=("frame_id", "count"))
).sort_values("cnt", ascending=False)

cnt
labels_set                                                                                                                                                
(share_challenge_box_white, guess_grey, refresh_btn, game_about_to_start_box_white, game_finished_well_done_big_box)                                  1166
(game_breakdown_blue, share_challenge_box_white, refresh_btn, game_about_to_start_box_white, guess_expanded)                                           599
(big_green_btw_rounds_box, participants_box, play_again, refresh_btn, game_about_to_start_box_white, play)                                             361
(big_green_btw_rounds_box, participants_box, play_again, refresh_btn, game_about_to_start_box_white)                                                   330
(share_challenge_box_white, refresh_btn, game_about_to_start_box_white, game_finished_white_box, guess_expanded)                                       309
(refresh_btn, play, play_todays_challenge_green, game_about_to_start_box_white)                                                                        269
(refresh_btn, game_about_to_start_box_white, share_challenge_box_white)                                                                                 68
(big_green_btw_rounds_box, play_again, status_bar_purple, refresh_btn, game_about_to_start_box_white)                                                   64
(big_green_btw_rounds_box, play_again, status_bar_purple, refresh_btn, game_about_to_start_box_white, play)                                             46
(guess_w_icon_only_expanded, status_bar_purple, refresh_btn, game_about_to_start_box_white, play)                                                       45
(guess_grey, refresh_btn, game_about_to_start_box_white, share_challenge_box_white)                                                                     38
(guess_expanded, refresh_btn, game_about_to_start_box_white, share_challenge_box_white)                                                                 28
(game_breakdown_blue, share_challenge_box_white, refresh_btn, game_about_to_start_box_white, game_finished_white_box, guess_expanded)                   18
(refresh_btn, challenge_btn_orange, play_current_leg, game_about_to_start_box_white)                                                                    15
(btw_rounds_points_bar_blue_wide, guess_w_icon_only_expanded, status_bar_purple, refresh_btn, game_about_to_start_box_white)                            14
(guess_w_icon_only_expanded, refresh_btn, game_about_to_start_box_white)                                                                                 9
(btw_rounds_points_bar_blue_wide, guess_w_icon_only_expanded, status_bar_purple, refresh_btn, game_about_to_start_box_white, play_current_leg)           8
(guess_w_icon_only_expanded, play, refresh_btn, game_about_to_start_box_white)                                                                           7
(btw_rounds_points_bar_blue_wide, guess_w_icon_only_expanded, refresh_btn, game_about_to_start_box_white, play, play_current_leg)                        6
(btw_rounds_points_bar_blue_wide, guess_w_icon_only_expanded, refresh_btn, game_about_to_start_box_white, play_current_leg)                              4
(btw_rounds_points_bar_blue_wide, guess_w_icon_only_expanded, status_bar_purple, refresh_btn, game_about_to_start_box_white, play)                       4
(game_breakdown, share_challenge_box_white, guess_grey, refresh_btn, game_about_to_start_box_white)                                                      3
(big_green_btw_rounds_box, participants_box, play_again, battle_royale_btw_rounds_red_box, refresh_btn, game_about_to_start_box_white, play)             3
(btw_rounds_points_bar_blue_wide, guess_w_icon_only_expanded, status_bar_purple, refresh_btn, game_about_to_start_box_white, play, play_current_leg)     3
(share_challenge_box_white, guess_grey, refresh_btn, game_about_to_start_box_white, game_finished_well_done_big_box, gues

### Show all Frames For game_state==unknown 

In [536]:
with pd.option_context("display.max_rows", None, "display.max_columns", None):
    display(
        df_framedets[df_framedets.game_state_smoothed == "unknown"][
            [
                "frame_id",
                "label_ids",
                "labels_set",
                "scores",
                "label_set_count",
                "seconds",
                "time",
                "game_state",
                "game_state_smoothed",
            ]
        ]
    )

frame_id                     label_ids  \
41          41          [10, 17, 29, 48, 55]   
42          42  [10, 17, 29, 46, 48, 55, 63]   
43          43      [10, 17, 29, 48, 55, 63]   
44          44          [10, 17, 29, 55, 63]   
45          45      [10, 17, 29, 46, 55, 63]   
46          46      [10, 17, 29, 46, 55, 63]   
47          47      [10, 17, 29, 46, 55, 63]   
48          48      [10, 17, 29, 46, 55, 63]   
49          49          [10, 17, 29, 55, 63]   
50          50          [10, 17, 29, 55, 63]   
51          51      [10, 17, 29, 48, 55, 63]   
52          52  [10, 17, 29, 46, 48, 55, 63]   
53          53      [10, 17, 29, 48, 55, 63]   
54          54      [10, 17, 29, 48, 55, 63]   
55          55          [10, 17, 29, 48, 55]   
56          56              [17, 29, 46, 55]   
57          57              [17, 29, 46, 55]   
58          58          [17, 29, 46, 55, 63]   
59          59          [17, 29, 46, 55, 63]   
60          60          [17, 29, 46, 55, 63]   
61          61          [17, 29, 46, 55, 63]   
62          62          [17, 29, 46, 55, 63]   
63          63          [17, 29, 46, 55, 63]   
64          64          [17, 29, 46, 55, 63]   
65          65          [17, 29, 46, 55, 63]   
66          66          [17, 29, 46, 55, 63]   
67          67          [17, 29, 46, 55, 63]   
68          68          [17, 29, 46, 55, 63]   
69          69          [17, 29, 46, 55, 63]   
70          70          [17, 29, 46, 55, 63]   
71          71          [17, 29, 46, 55, 63]   
72          72          [17, 29, 46, 55, 63]   
73          73          [17, 29, 46, 55, 63]   
74          74          [17, 29, 46, 55, 63]   
75          75          [17, 29, 46, 55, 63]   
76          76          [17, 29, 46, 55, 63]   
77          77          [17, 29, 46, 55, 63]   
78          78          [17, 29, 46, 55, 63]   
79          79          [17, 29, 46, 55, 63]   
80          80          [17, 29, 46, 55, 63]   
81          81          [17, 29, 46, 55, 63]   
82          82          [17, 29, 46, 55, 63]   
83          83          [17, 29, 46, 55, 63]   
84          84          [17, 29, 46, 55, 63]   
85          85          [17, 29, 46, 55, 63]   
86          86          [17, 29, 46, 55, 63]   
87          87          [17, 29, 46, 55, 63]   
88          88          [17, 29, 46, 55, 63]   
89          89          [17, 29, 46, 55, 63]   
90          90          [17, 29, 46, 55, 63]   
91          91          [17, 29, 46, 55, 63]   
92          92          [17, 29, 46, 55, 63]   
93          93          [17, 29, 46, 55, 63]   
94          94          [17, 29, 46, 55, 63]   
95          95          [17, 29, 46, 55, 63]   
96          96          [17, 29, 46, 55, 63]   
97          97          [17, 29, 46, 55, 63]   
98          98          [17, 29, 46, 55, 63]   
99          99          [17, 29, 46, 55, 63]   
100        100          [17, 29, 46, 55, 63]   
101        101          [17, 29, 46, 55, 63]   
102        102          [17, 29, 46, 55, 63]   
103        103              [17, 29, 46, 55]   
104        104                  [17, 29, 55]   
105        105                  [17, 29, 55]   
106        106              [11, 17, 48, 55]   
107        107              [11, 17, 48, 55]   
108        108              [11, 17, 48, 55]   
109        109              [11, 17, 48, 55]   
110        110                  [17, 55, 57]   
111        111                  [17, 55, 57]   
112        112                  [17, 55, 57]   
113        113          [17, 20, 26, 55, 57]   
114        114          [17, 20, 26, 55, 57]   
115        115          [17, 20, 26, 55, 57]   
116        116          [17, 20, 26, 55, 57]   
117        117          [17, 20, 26, 55, 57]   
118        118          [17, 20, 26, 55, 57]   
119        119          [17, 20, 26, 55, 57]   
120        120          [17, 20, 26, 55, 57]   
121        121      [17, 20, 26, 29, 55, 57]   
122        122          [17, 20, 26, 55, 57]   
123        123        

In [537]:
with pd.option_context("display.max_rows", None, "display.max_columns", None):
    display(
        df_framedets[df_framedets.frame_id >= 3966][
            [
                "frame_id",
                "label_ids",
                "labels_set",
                "scores",
                "label_set_count",
                "seconds",
                "time",
                "game_state",
                "game_state_smoothed",
            ]
        ]
    )

Empty DataFrame
Columns: [frame_id, label_ids, labels_set, scores, label_set_count, seconds, time, game_state, game_state_smoothed]
Index: []

### Find frames that have a specific set of UI elements

In [519]:
df_framedets[df_framedets.labels_set == ("status_bar_white", "other", "status_bar", "game_title")]

Empty DataFrame
Columns: [frame_id, label_ids, labels, labels_set, scores, bboxes, label_set_count, seconds, time, game_state, game_state_smoothed]
Index: []

---

## Segment many videos at once

In [421]:
segments = {}
val_ids = [
    "AF9uezxZDeE",
    "9RQUIk1OwAY",
    "S5Ne5eoHxsY",
    "nyHeQWnm8YA",
    "hZWt1PYH3hI",
    "dY1RXh-43q4",
    "83m9ys4kxro",
    "osTwgzWluVs",
    "o8qQAjkaXMM",
]
for video_id in val_ids:
    print("")
    print("video_id: ", video_id)
    df_framedets = load_detections(video_id)
    df_framedets["game_state"] = df_framedets.apply(classify_frame, axis=1)
    apply_smoothing(df_framedets)
    seg = get_segments(df_framedets)
    segments[video_id] = get_oog_segments(seg)


video_id:  AF9uezxZDeE

video_id:  9RQUIk1OwAY

video_id:  S5Ne5eoHxsY

video_id:  nyHeQWnm8YA

video_id:  hZWt1PYH3hI

video_id:  dY1RXh-43q4

video_id:  83m9ys4kxro

video_id:  osTwgzWluVs

video_id:  o8qQAjkaXMM


In [423]:
for video_id, seg in segments.items():
    print("")
    print("video_id: ", video_id)
    # display(seg)
    for s in seg:
        print(s)


video_id:  AF9uezxZDeE
{'state': 'out_of_game', 'start_frame_id': 554, 'start_frame_time': 138.5, 'end_frame_id': 567, 'end_frame_time': 141.75}
{'state': 'out_of_game', 'start_frame_id': 992, 'start_frame_time': 248.0, 'end_frame_id': 1104, 'end_frame_time': 276.0}
{'state': 'out_of_game', 'start_frame_id': 1373, 'start_frame_time': 343.25, 'end_frame_id': 1409, 'end_frame_time': 352.25}
{'state': 'out_of_game', 'start_frame_id': 1754, 'start_frame_time': 438.5, 'end_frame_id': 1762, 'end_frame_time': 440.5}
{'state': 'out_of_game', 'start_frame_id': 2246, 'start_frame_time': 561.5, 'end_frame_id': 2809, 'end_frame_time': 702.25}

video_id:  9RQUIk1OwAY
{'state': 'out_of_game', 'start_frame_id': 741, 'start_frame_time': 185.25, 'end_frame_id': 850, 'end_frame_time': 212.5}
{'state': 'out_of_game', 'start_frame_id': 1576, 'start_frame_time': 394.0, 'end_frame_id': 1663, 'end_frame_time': 415.75}
{'state': 'out_of_game', 'start_frame_id': 2388, 'start_frame_time': 597.0, 'end_frame_id'

### Show the game states sequence:

In [339]:
with pd.option_context("display.max_rows", None, "display.max_columns", None):
    display(
        df_framedets[df_framedets.seconds.isin([702.25, 702.5])][
            ["labels_set", "game_state", "time", "seconds"]
        ]
    )
    # display(df_framedets[["labels_set", "game_state", "time", "seconds"]])

labels_set game_state             time  seconds
2809  (in_game_map_expanded,)    unknown  00:11:42:250000   702.25
2810  (in_game_map_expanded,)    unknown  00:11:42:500000   702.50

In [262]:
df_framedets.game_state.unique()

array(['pre_game', 'between_round_or_game_ambiguous', 'unknown', 'between_games', 'in_game', 'between_rounds', 'out_of_game'], dtype=object)

game_state
0                           (pre_game, 4)
1                           (pre_game, 4)
2                           (pre_game, 4)
3                           (pre_game, 4)
4                           (pre_game, 4)
5                           (pre_game, 4)
6                           (pre_game, 4)
7                           (pre_game, 4)
8                           (pre_game, 4)
9                           (pre_game, 4)
10                          (pre_game, 4)
11                          (pre_game, 4)
12                          (pre_game, 4)
13                          (pre_game, 4)
14                          (pre_game, 4)
15                          (pre_game, 4)
16                          (pre_game, 4)
17                          (pre_game, 4)
18                          (pre_game, 4)
19                          (pre_game, 4)
20                          (pre_game, 4)
21                          (pre_game, 4)
22                          (pre_game, 4)
23                          (pre_game, 4)
24                          (pre_game, 4)
25                          (pre_game, 4)
26                          (pre_game, 4)
27                          (pre_game, 4)
28                          (pre_game, 4)
29                          (pre_game, 4)
30                          (pre_game, 4)
31                          (pre_game, 4)
32                          (pre_game, 4)
33                          (pre_game, 4)
34                          (pre_game, 4)
35                          (pre_game, 4)
36                          (pre_game, 4)
37                          (pre_game, 4)
38                          (pre_game, 4)
39                          (pre_game, 4)
40                          (pre_game, 4)
41                          (pre_game, 4)
42                          (pre_game, 4)
43                          (pre_game, 4)
44                          (pre_game, 4)
45                          (pre_game, 4)
46                          (pre_game, 4)
47                          (pre_game, 4)
48                          (pre_game, 4)
49                          (pre_game, 4)
50                          (pre_game, 4)
51                          (pre_game, 4)
52                          (pre_game, 4)
53                          (pre_game, 4)
54                          (pre_game, 4)
55                          (pre_game, 4)
56                          (pre_game, 4)
57                          (pre_game, 4)
58                          (pre_game, 4)
59                          (pre_game, 4)
60                          (pre_game, 4)
61                          (pre_game, 4)
62                          (pre_game, 4)
63                          (pre_game, 4)
64                          (pre_game, 4)
65                          (pre_game, 4)
66                          (pre_game, 4)
67                          (pre_game, 4)
68                          (pre_game, 4)
69                          (pre_game, 4)
70                          (pre_game, 4)
71                          (pre_game, 4)
72                          (pre_game, 4)
73                          (pre_game, 4)
74                          (pre_game, 4)
75                          (pre_game, 4)
76                          (pre_game, 4)
77                          (pre_game, 4)
78                          (pre_game, 4)
79                          (pre_game, 4)
80                          (pre_game, 4)
81                          (pre_game, 4)
82                          (pre_game, 4)
83                          (pre_game, 4)
84                          (pre_game, 4)
85                          (pre_game, 4)
86                          (pre_game, 4)
87                          (pre_game, 4)
88                          (pre_game, 4)
89                          (pre_game, 4)
90                          (pre_game, 4)
91                          (pre_game, 4)
92                          (pre_game, 4)
93                          (pre_game, 4)
94                          (pre_game, 4)

In [266]:
current_state = "out_of_game"
state_transitions = []
for i, row in df_framedets.iterrows():
    if current_state != "in_game" and row.game_state == "in_game":
        state_transitions.extend(
            [
                {
                    "state": "out_of_game",
                    "end_frame_id": row.frame_id,
                    "end_frame_time": row.seconds,
                },
                {
                    "state": "in_game",
                    "start_frame_id": row.frame_id,
                    "start_frame_time": row.seconds,
                },
            ]
        )
        current_state = "in_game"
    elif current_state == "in_game":
        if row.game_state == "in_game":
            continue
        else:
            state_transitions.extend(
                [
                    {
                        "state": "in_game",
                        "end_frame_id": row.frame_id,
                        "end_frame_time": row.seconds,
                    },
                    {
                        "state": "out_of_game",
                        "start_frame_id": row.frame_id,
                        "start_frame_time": row.seconds,
                    },
                ]
            )
            current_state = row.game_state

state_transitions

[{'state': 'out_of_game', 'end_frame_id': 158, 'end_frame_time': 39.5},
 {'state': 'in_game', 'start_frame_id': 158, 'start_frame_time': 39.5},
 {'state': 'in_game', 'end_frame_id': 554, 'end_frame_time': 138.5},
 {'state': 'out_of_game', 'start_frame_id': 554, 'start_frame_time': 138.5},
 {'state': 'out_of_game', 'end_frame_id': 567, 'end_frame_time': 141.75},
 {'state': 'in_game', 'start_frame_id': 567, 'start_frame_time': 141.75},
 {'state': 'in_game', 'end_frame_id': 992, 'end_frame_time': 248.0},
 {'state': 'out_of_game', 'start_frame_id': 992, 'start_frame_time': 248.0},
 {'state': 'out_of_game', 'end_frame_id': 1104, 'end_frame_time': 276.0},
 {'state': 'in_game', 'start_frame_id': 1104, 'start_frame_time': 276.0},
 {'state': 'in_game', 'end_frame_id': 1373, 'end_frame_time': 343.25},
 {'state': 'out_of_game', 'start_frame_id': 1373, 'start_frame_time': 343.25},
 {'state': 'out_of_game', 'end_frame_id': 1409, 'end_frame_time': 352.25},
 {'state': 'in_game', 'start_frame_id': 140

## Scratch / Junk

---


In [157]:
with pd.option_context("display.max_rows", None, "display.max_columns", None):
    display(
        df_framedets.loc[230:490][
            [
                "frame_id",
                "seconds",
                "labels",
                "labels_set",
                "game_state",
                "scores",
            ]
        ]
    )

frame_id  seconds  \
230       230    57.50   
231       231    57.75   
232       232    58.00   
233       233    58.25   
234       234    58.50   
235       235    58.75   
236       236    59.00   
237       237    59.25   
238       238    59.50   
239       239    59.75   
240       240    60.00   
241       241    60.25   
242       242    60.50   
243       243    60.75   
244       244    61.00   
245       245    61.25   
246       246    61.50   
247       247    61.75   
248       248    62.00   
249       249    62.25   
250       250    62.50   
251       251    62.75   
252       252    63.00   
253       253    63.25   
254       254    63.50   
255       255    63.75   
256       256    64.00   
257       257    64.25   
258       258    64.50   
259       259    64.75   
260       260    65.00   
261       261    65.25   
262       262    65.50   
263       263    65.75   
264       264    66.00   
265       265    66.25   
266       266    66.50   
267       267    66.75   
268       268    67.00   
269       269    67.25   
270       270    67.50   
271       271    67.75   
272       272    68.00   
273       273    68.25   
274       274    68.50   
275       275    68.75   
276       276    69.00   
277       277    69.25   
278       278    69.50   
279       279    69.75   
280       280    70.00   
281       281    70.25   
282       282    70.50   
283       283    70.75   
284       284    71.00   
285       285    71.25   
286       286    71.50   
287       287    71.75   
288       288    72.00   
289       289    72.25   
290       290    72.50   
291       291    72.75   
292       292    73.00   
293       293    73.25   
294       294    73.50   
295       295    73.75   
296       296    74.00   
297       297    74.25   
298       298    74.50   
299       299    74.75   
300       300    75.00   
301       301    75.25   
302       302    75.50   
303       303    75.75   
304       304    76.00   
305       305    76.25   
306       306    76.50   
307       307    76.75   
308       308    77.00   
309       309    77.25   
310       310    77.50   
311       311    77.75   
312       312    78.00   
313       313    78.25   
314       314    78.50   
315       315    78.75   
316       316    79.00   
317       317    79.25   
318       318    79.50   
319       319    79.75   
320       320    80.00   
321       321    80.25   
322       322    80.50   
323       323    80.75   
324       324    81.00   
325       325    81.25   
326       326    81.50   
327       327    81.75   
328       328    82.00   
329       329    82.25   
330       330    82.50   
331       331    82.75   
332       332    83.00   
333       333    83.25   
334       334    83.50   
335       335    83.75   
336       336    84.00   
337       337    84.25   
338       338    84.50   
339       339    84.75   
340       340    85.00   
341       341    85.25   
342       342    85.50   
343       343    85.75   
344       344    86.00   
345       345    86.25   
346       346    86.50   
347       347    86.75   
348       348    87.00   
349       349    87.25   
350       350    87.50   
351       351    87.75   
352       352    88.00   
353       353    88.25   
354       354    88.50   
355       355    88.75   
356       356    89.00   
357       357    89.25   
358       358    89.50   
359       359    89.75   
360       360    90.00   
361       361    90.25   
362       362    90.50   
363       363    90.75   
364       364    91.00   
365       365    91.25   
366       366    91.50   
367       367    91.75   
368       368    92.00   
369       369    92.25   
370       370    92.50   
371       371    92.75   
372       372    93.00   
373       373    93.25   
374       374    93.50   
375       375    93.75   
376       376    94.00   
377       377    94.25   
378       378    94.50   
379       379    94.75   
380       380    95.00   
381       381    95.25   
382       382    95.50   
3

In [164]:
with pd.option_context("display.max_rows", None, "display.max_columns", None):
    display(df_framedets.tail(100))

frame_id             label_ids  \
6228      6228  [17, 46, 52, 55, 57]   
6229      6229  [17, 46, 52, 55, 57]   
6230      6230  [17, 46, 52, 55, 57]   
6231      6231  [17, 46, 52, 55, 57]   
6232      6232  [17, 46, 52, 55, 57]   
6233      6233  [17, 46, 52, 55, 57]   
6234      6234  [17, 46, 52, 55, 57]   
6235      6235  [17, 46, 52, 55, 57]   
6236      6236  [17, 46, 52, 55, 57]   
6237      6237  [17, 46, 52, 55, 57]   
6238      6238  [17, 46, 52, 55, 57]   
6239      6239  [17, 46, 52, 55, 57]   
6240      6240  [17, 46, 52, 55, 57]   
6241      6241  [17, 46, 52, 55, 57]   
6242      6242  [17, 46, 52, 55, 57]   
6243      6243  [17, 46, 52, 55, 57]   
6244      6244  [17, 46, 52, 55, 57]   
6245      6245  [17, 46, 52, 55, 57]   
6246      6246  [17, 46, 52, 55, 57]   
6247      6247  [17, 46, 52, 55, 57]   
6248      6248  [17, 46, 52, 55, 57]   
6249      6249  [17, 46, 52, 55, 57]   
6250      6250  [17, 46, 52, 55, 57]   
6251      6251  [17, 46, 52, 55, 57]   
6252      6252      [17, 46, 52, 55]   
6253      6253  [17, 46, 52, 55, 57]   
6254      6254  [17, 46, 52, 55, 57]   
6255      6255  [17, 46, 52, 55, 57]   
6256      6256  [17, 46, 52, 55, 57]   
6257      6257  [17, 46, 52, 55, 57]   
6258      6258  [17, 46, 52, 55, 57]   
6259      6259  [17, 46, 52, 55, 57]   
6260      6260  [17, 46, 52, 55, 57]   
6261      6261  [17, 46, 52, 55, 57]   
6262      6262  [17, 46, 52, 55, 57]   
6263      6263  [17, 46, 52, 55, 57]   
6264      6264  [17, 46, 52, 55, 57]   
6265      6265  [17, 46, 52, 55, 57]   
6266      6266  [17, 46, 52, 55, 57]   
6267      6267  [17, 46, 52, 55, 57]   
6268      6268  [17, 46, 52, 55, 57]   
6269      6269  [17, 46, 52, 55, 57]   
6270      6270  [17, 46, 52, 55, 57]   
6271      6271  [17, 46, 52, 55, 57]   
6272      6272  [17, 46, 52, 55, 57]   
6273      6273  [17, 46, 52, 55, 57]   
6274      6274  [17, 46, 52, 55, 57]   
6275      6275      [17, 46, 52, 55]   
6276      6276      [17, 46, 52, 55]   
6277      6277  [17, 46, 52, 55, 57]   
6278      6278  [17, 46, 52, 55, 57]   
6279      6279  [17, 46, 52, 55, 57]   
6280      6280  [17, 46, 52, 55, 57]   
6281      6281  [17, 46, 52, 55, 57]   
6282      6282  [17, 46, 52, 55, 57]   
6283      6283  [17, 46, 52, 55, 57]   
6284      6284  [17, 46, 52, 55, 57]   
6285      6285  [17, 46, 52, 55, 57]   
6286      6286  [17, 46, 52, 55, 57]   
6287      6287  [17, 46, 52, 55, 57]   
6288      6288  [17, 46, 52, 55, 57]   
6289      6289  [17, 46, 52, 55, 57]   
6290      6290  [17, 46, 52, 55, 57]   
6291      6291  [17, 46, 52, 55, 57]   
6292      6292  [17, 46, 52, 55, 57]   
6293      6293  [17, 46, 52, 55, 57]   
6294      6294  [17, 46, 52, 55, 57]   
6295      6295  [17, 46, 52, 55, 57]   
6296      6296  [17, 46, 52, 55, 57]   
6297      6297  [17, 46, 52, 55, 57]   
6298      6298  [17, 46, 52, 55, 57]   
6299      6299  [17, 46, 52, 55, 57]   
6300      6300  [17, 46, 52, 55, 57]   
6301      6301  [17, 46, 52, 55, 57]   
6302      6302  [17, 46, 52, 55, 57]   
6303      6303  [17, 46, 52, 55, 57]   
6304      6304  [17, 46, 52, 55, 57]   
6305      6305  [17, 46, 52, 55, 57]   
6306      6306  [17, 46, 52, 55, 57]   
6307      6307  [17, 46, 52, 55, 57]   
6308      6308  [17, 46, 52, 55, 57]   
6309      6309  [17, 46, 52, 55, 57]   
6310      6310  [17, 46, 52, 55, 57]   
6311      6311  [17, 46, 52, 55, 57]   
6312      6312  [17, 46, 52, 55, 57]   
6313      6313  [17, 46, 52, 55, 57]   
6314      6314  [17, 46, 52, 55, 57]   
6315      6315  [17, 46, 52, 55, 57]   
6316      6316  [17, 46, 52, 55, 57]   
6317      6317  [17, 46, 52, 55, 57]   
6318      6318  [17, 46, 52, 55, 57]   
6319      6319  [17, 46, 52, 55, 57]   
6320      6320  [17, 46, 52, 55, 57]   
6321      6321  [17, 46, 52, 55, 57]   
6322      6322  [17, 46, 52, 55, 57]   
6323      6323  [17, 46, 52, 55, 57]   
6324      6324  [17, 46, 52, 55, 57]   
6325      6325  [17, 46, 52, 55, 57]   
6326      6326  [17, 46, 52, 55, 57]   
6327  

---